In [ ]:
!pip install transformers datasets
! pip install -U accelerate
! pip install -U transformers


     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 547.8/547.8 kB 3.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 39.9/39.9 MB 13.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 8.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 64.9/64.9 kB 813.6 kB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.1/194.1 kB 7.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 9.2 MB/s eta 0:00:00
  Attempting uninstall: requests
    Found existing installation: requests 2.31.0
    Uninstalling requests-2.31.0:
      Successfully uninstalled requests-2.31.0
  Attempting uninstall: pyarrow
    Found existing installation: pyarrow 14.0.2
    Uninstalling pyarrow-14.0.2:
      Successfully uninstalled pyarrow-14.0.2
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
cudf-cu12 24

In [ ]:
import accelerate
import transformers

import pandas as pd
from google.colab import drive
import ast
from datasets import Dataset
from transformers import AutoTokenizer, AutoModelForSeq2SeqLM, Seq2SeqTrainer, Seq2SeqTrainingArguments


transformers.__version__, accelerate.__version__

('4.42.4', '0.32.1')

In [ ]:
# prompt: mount drive

from google.colab import drive
drive.mount('/content/drive')


Mounted at /content/drive


In [ ]:
file_path = '/content/drive/MyDrive/upload/engnivkal.txt'

# Read the file contents
with open(file_path, 'r') as file:
  contents = file.read()

print(contents)


[[" In the beginning God created the heavens and the earth.", "[start] Eng' taunet, ko ki toi Kamuktaindet koyai kipsengwet ak ng'wony. [end]"], [" Now the earth was formless and empty, darkness was over the surface of the deep, and the Spirit of God was hovering over the waters.", "[start] Ki ma komi kiy ng'wony ak ki ma kotinyei itoon age tugul. Ki mi mesundeito paragutap rireet ak ki wendoti Kabuusetap Kamuktaindet eng' paragutap peek. [end]"], [" And God said, \u201cLet there be light,\u201d and there was light.", "[start]  Komwa Kamuktaindet kole, \u201cIngolapkeiit\u201d ak ki lapkeiit. [end]"], [" God saw that the light was good, and he separated the light from the darkness.", "[start] Kogeer anyun Kamuktaindet lapkeiyet kole myee, koobeesyo lapkeiyet ak mesundeito. [end]"], [" God called the light \u201cday,\u201d and the darkness he called \u201cnight.\u201d And there was evening, and there was morning\u2014the first day.", "[start] Ki kuure Kamuktaindet lapkeiyet Peet ak kogu

In [ ]:
# Convert the contents from string to list of lists
data = ast.literal_eval(contents)

# Create a DataFrame
df = pd.DataFrame(data, columns=['English', 'Kalenjin'])

# Remove the '[start]' and '[end]' tags from the Kalenjin column
df['Kalenjin'] = df['Kalenjin'].str.replace('[start]', '').str.replace('[end]', '').str.strip()

df.tail()

English  \
30388   The Spirit and the bride say, “Come!” And let...   
30389   I warn everyone who hears the words of the pr...   
30390   And if anyone takes words away from this scro...   
30391   He who testifies to these things says, “Yes, ...   
30392   The grace of the Lord Jesus be with God’s peo...   

                                                Kalenjin  
30388  Mwaei Kabuuset ne Tiliil ak murereet kole, “Ny...  
30389  Abaoryanjini chii age tugul ne kasei ng'aleek ...  
30390  Ak ngo nem chii age tugul ng'aleek eng' bukuit...  
30391  Mwaei ineendet ne paoryanjin tuguuchu kole, “E...  
30392  Ingotep myeeindap Kiptaiyat Jeso Kristo koboot...

In [ ]:
df.shape

(30393, 2)

In [ ]:
# from google.colab import files

# df.to_excel('engnivkal.xlsx', index=False)  # Save DataFrame to Excel file

# files.download('engnivkal.xlsx')  # Download the Excel file


In [ ]:
# Convert DataFrame to Hugging Face Dataset
dataset = Dataset.from_pandas(df)

In [ ]:

tokenizer = AutoTokenizer.from_pretrained("Helsinki-NLP/opus-mt-en-mul")
model = AutoModelForSeq2SeqLM.from_pretrained("Helsinki-NLP/opus-mt-en-mul")
# tokenizer = AutoTokenizer.from_pretrained(model_name)
# model = AutoModelForSeq2SeqLM.from_pretrained(model_name)

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:99: UserWarning: 
Error while fetching `HF_TOKEN` secret value from your vault: 'Requesting secret HF_TOKEN timed out. Secrets can only be fetched when running from the Colab UI.'.
You are not authenticated with the Hugging Face Hub in this notebook.
If the error persists, please let us know by opening an issue on GitHub (https://github.com/huggingface/huggingface_hub/issues/new).
  warnings.warn(


tokenizer_config.json:   0%|          | 0.00/44.0 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/1.40k [00:00<?, ?B/s]

source.spm:   0%|          | 0.00/790k [00:00<?, ?B/s]

target.spm:   0%|          | 0.00/707k [00:00<?, ?B/s]

vocab.json:   0%|          | 0.00/1.42M [00:00<?, ?B/s]

/usr/local/lib/python3.10/dist-packages/transformers/models/marian/tokenization_marian.py:175: UserWarning: Recommended: pip install sacremoses.
  warnings.warn("Recommended: pip install sacremoses.")


pytorch_model.bin:   0%|          | 0.00/310M [00:00<?, ?B/s]

generation_config.json:   0%|          | 0.00/293 [00:00<?, ?B/s]

In [ ]:
# Tokenize the data
def preprocess_function(examples):
    inputs = examples['English']
    targets = examples['Kalenjin']
    model_inputs = tokenizer(inputs, max_length=128, truncation=True, padding="max_length")

    with tokenizer.as_target_tokenizer():
        labels = tokenizer(targets, max_length=128, truncation=True, padding="max_length")

    model_inputs["labels"] = labels["input_ids"]
    return model_inputs

tokenized_dataset = dataset.map(preprocess_function, batched=True)
tokenized_dataset

Map:   0%|          | 0/30393 [00:00<?, ? examples/s]

/usr/local/lib/python3.10/dist-packages/transformers/tokenization_utils_base.py:4016: UserWarning: `as_target_tokenizer` is deprecated and will be removed in v5 of Transformers. You can tokenize your labels by using the argument `text_target` of the regular `__call__` method (either in the same call as your input texts if you use the same keyword arguments, or in a separate call.
  warnings.warn(


Dataset({
    features: ['English', 'Kalenjin', 'input_ids', 'attention_mask', 'labels'],
    num_rows: 30393
})

In [ ]:
# Split the dataset into train and test sets
train_test_split = tokenized_dataset.train_test_split(test_size=0.1)
train_dataset = train_test_split["train"]
test_dataset = train_test_split["test"]

In [ ]:
# Set training arguments
training_args = Seq2SeqTrainingArguments(
    output_dir="./results",
    evaluation_strategy="epoch",
    learning_rate=2e-5,
    per_device_train_batch_size=16,
    per_device_eval_batch_size=16,
    weight_decay=0.01,
    save_total_limit=5,
    num_train_epochs=5,
    predict_with_generate=True,
    fp16=True,
)

/usr/local/lib/python3.10/dist-packages/transformers/training_args.py:1494: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(


In [ ]:
# Initialize the Trainer
trainer = Seq2SeqTrainer(
    model=model,
    args=training_args,
    train_dataset=train_dataset,
    eval_dataset=test_dataset,
    tokenizer=tokenizer,
)

In [ ]:
# Train the model
trainer.train()

Some non-default generation parameters are set in the model config. These should go into a GenerationConfig file (https://huggingface.co/docs/transformers/generation_strategies#save-a-custom-decoding-strategy-with-your-model) instead. This warning will be raised to an exception in v4.41.
Non-default generation parameters: {'max_length': 512, 'num_beams': 4, 'bad_words_ids': [[64109]], 'forced_eos_token_id': 0}
Some non-default generation parameters are set in the model config. These should go into a GenerationConfig file (https://huggingface.co/docs/transformers/generation_strategies#save-a-custom-decoding-strategy-with-your-model) instead. This warning will be raised to an exception in v4.41.
Non-default generation parameters: {'max_length': 512, 'num_beams': 4, 'bad_words_ids': [[64109]], 'forced_eos_token_id': 0}
Some non-default generation parameters are set in the model config. These should go into a GenerationConfig file (https://huggingface.co/docs/transformers/generation_strate

TrainOutput(global_step=8550, training_loss=0.6873195599115383, metrics={'train_runtime': 1591.9796, 'train_samples_per_second': 85.909, 'train_steps_per_second': 5.371, 'total_flos': 4636109879377920.0, 'train_loss': 0.6873195599115383, 'epoch': 5.0})

In [ ]:
evaluation_results = trainer.evaluate()
print(f"Evaluation results: {evaluation_results}")


Evaluation results: {'eval_loss': 0.5533947944641113, 'eval_runtime': 10.0125, 'eval_samples_per_second': 303.621, 'eval_steps_per_second': 18.976, 'epoch': 5.0}


In [ ]:
!pip install torch
import torch

test_sentences = [
    "Hello friend.",
    "bear fruit."
]

inputs = tokenizer(test_sentences, return_tensors="pt", padding=True, truncation=True, max_length=128)

# Move inputs to the GPU if available
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
inputs = {k: v.to(device) for k, v in inputs.items()}

with torch.no_grad():
    outputs = model.generate(inputs["input_ids"], max_length=128)

translations = [tokenizer.decode(output, skip_special_tokens=True) for output in outputs]

for i, translation in enumerate(translations):
    print(f"English: {test_sentences[i]}")
    print(f"Kalenjin: {translation}")

English: Hello friend.
Kalenjin: Alo chorweet.
English: bear fruit.
Kalenjin: igoitoi logoek.


In [ ]:
# prompt: save model

trainer.save_model("my_kalenjin_translation_model")
# Save the model and tokenizer
model.save_pretrained("./my_kalenjin_translator")
tokenizer.save_pretrained("./my_kalenjin_translator")


Some non-default generation parameters are set in the model config. These should go into a GenerationConfig file (https://huggingface.co/docs/transformers/generation_strategies#save-a-custom-decoding-strategy-with-your-model) instead. This warning will be raised to an exception in v4.41.
Non-default generation parameters: {'max_length': 512, 'num_beams': 4, 'bad_words_ids': [[64109]], 'forced_eos_token_id': 0}
Some non-default generation parameters are set in the model config. These should go into a GenerationConfig file (https://huggingface.co/docs/transformers/generation_strategies#save-a-custom-decoding-strategy-with-your-model) instead. This warning will be raised to an exception in v4.41.
Non-default generation parameters: {'max_length': 512, 'num_beams': 4, 'bad_words_ids': [[64109]], 'forced_eos_token_id': 0}


('./my_kalenjin_translator/tokenizer_config.json',
 './my_kalenjin_translator/special_tokens_map.json',
 './my_kalenjin_translator/vocab.json',
 './my_kalenjin_translator/source.spm',
 './my_kalenjin_translator/target.spm',
 './my_kalenjin_translator/added_tokens.json')

In [ ]:
# !pip install shutil
import shutil

# Compress the directory
shutil.make_archive('drive/MyDrive/final/my_kalenjin_translator', 'zip', './my_kalenjin_translator')


'/content/drive/MyDrive/final/my_kalenjin_translator.zip'

In [ ]:
from google.colab import files

# Download the file
files.download('/content/my_kalenjin_translation_model')


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [1]:
from google.colab import drive
drive.mount('/content/drive')


Mounted at /content/drive


In [4]:
import zipfile

# Path to the zip file
zip_path = '/content/drive/MyDrive/final/my_kalenjin_translator.zip'

# Unzip the model
with zipfile.ZipFile(zip_path, 'r') as zip_ref:
    zip_ref.extractall('/content/drive/MyDrive/final/my_kalenjin_translator')



In [2]:
from transformers import MarianMTModel, MarianTokenizer

# Load the model and tokenizer
model_path = 'my_kalenjin_translator'
tokenizer = MarianTokenizer.from_pretrained(model_path)
model = MarianMTModel.from_pretrained(model_path)


OSError: Incorrect path_or_model_id: './my_kalenjin_translator'. Please provide either the path to a local folder or the repo_id of a model on the Hub.

In [ ]:
import torch
# Function to test the model
def translate_text(text, tokenizer, model):
    inputs = tokenizer(text, return_tensors="pt", padding=True, truncation=True, max_length=128)
    with torch.no_grad():
        outputs = model.generate(inputs["input_ids"], max_length=128)
    translation = tokenizer.decode(outputs[0], skip_special_tokens=True)
    return translation

# Example text to translate
example_text = " I have learned to be content whatever the circumstances"

# Get the translation
translated_text = translate_text(example_text, tokenizer, model)
translated_text


"Ki koneetkei ale achame age tugul eng' ng'olyoondoniito."